In [1]:
import pandas as pd
import itertools
import matplotlib.pyplot as plt

import numpy as np
import seaborn as sns
from tqdm import tqdm
from matplotlib.colors import LogNorm
from scipy.cluster.hierarchy import linkage, dendrogram
from scipy.spatial.distance import squareform
from sklearn.metrics.cluster import adjusted_rand_score
from sklearn.metrics.cluster import normalized_mutual_info_score
from scipy.cluster.hierarchy import fcluster,dendrogram,linkage
from scipy.cluster.hierarchy import dendrogram

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
def load_matrix(embedding,modification):
    """
    Load the matrix from the file
    """
    # Load the matrix from the file
    test_df = pd.read_csv(f'/content/drive/MyDrive/data/briney/cluster_matrixes/{embedding}_{modification}.csv',index_col=0)
    # Defining the number of patient in dataset - number of clusters
    clust = [x.split('_')[0] for x in test_df.columns]
    # Coding patients for their clusters for comparison with model prediction
    patients_dict = {'316188':0, '326650':1, '326651':2,'326713':3, '326737':4,
                     '326780':5,'326797':6, '326907':7,'327059':8, 'D103':9}
    clust_as_float = [patients_dict[x] for x in clust]
    patients = set([x.split('_')[0] for x in test_df.columns])
    colors_for_w2 = sns.color_palette()[0:len(patients)]
    color_dict = dict(zip(patients,colors_for_w2))

    # a bit of rescaling of distances
    matrix=test_df.values
    matrix=matrix/matrix.mean()
    matrix=matrix/matrix.std()
    palette = []
    for sample in test_df.columns.tolist():
        palette.append(color_dict[sample.split('_')[0]])
    # Convert the matrix to a numpy array
    return matrix,clust,palette

def seriation(Z,N,cur_index):
    '''Seriation computes the order implied by a hierarchical tree (dendrogram)
    Args:
        - Z is a hierarchical tree (dendrogram)
        - N is the number of points given to the clustering process
        - cur_index is the position in the tree for the recursive traversal
    Returns:
        - order implied by the hierarchical tree Z
    '''
    if cur_index < N: return [cur_index]
    else:
        left = int(Z[cur_index-N,0])
        right = int(Z[cur_index-N,1])
    return (seriation(Z,N,left) + seriation(Z,N,right))

def compute_serial_matrix(dist_mat,method="ward"):
    '''Compute_serial_matrix transforms a distance matrix into
       a sorted distance matrix according to the order implied
       by the hierarchical tree (dendrogram).
    Args:
        - dist_mat is a distance matrix
        - method = ["ward","single","average","complete"]
    Returns:
        - seriated_dist is the input dist_mat,
          but with re-ordered rows and columns
          according to the seriation, i.e. the
          order implied by the hierarchical tree
        - res_order is the order implied by
          the hierarhical tree
        - res_linkage is the hierarhical tree (dendrogram)
    '''
    N = len(dist_mat)
    flat_dist_mat = squareform(dist_mat)
    res_linkage = linkage(flat_dist_mat, method=method)
    res_order = seriation(res_linkage, N, N + N-2)
    seriated_dist = np.zeros((N,N))
    a,b = np.triu_indices(N,k=1)
    seriated_dist[a,b] = dist_mat[ [res_order[i] for i in a], [res_order[j] for j in b]]
    seriated_dist[b,a] = seriated_dist[a,b]
    return seriated_dist, res_order, res_linkage

def get_clusters(matrix,threshold=0.1,method='ward'):
    """
    Get clusters from the matrix
    """
    flat_dist_mat = squareform(np.array(matrix))
    res_linkage = linkage(flat_dist_mat, method=method)
    clusters = fcluster(res_linkage, t=threshold, criterion='distance')
    return clusters

def get_rand_score(embedding,modification,method='ward'):
    """
    Get the rand score for the given embedding and modification
    """
    # Reading the data
    test_df = pd.read_csv(f'/content/drive/MyDrive/data/briney/cluster_matrixes/{embedding}_{modification}.csv',index_col=0)

    # Defining the number of patient in dataset - number of clusters
    clust = [x.split('_')[0] for x in test_df.columns]
    matrix= test_df.values/test_df.values.mean()
    mean_val = test_df.values.mean()
    std_val=matrix.std()
    # Coding patients for their clusters for comparison with model prediction
    patients_dict = {'316188':0, '326650':1, '326651':2, '326713':3,
                    '326737':4, '326780':5, '326797':6, '326907':7, '327059':8, 'D103':9}
    clust_as_float = [patients_dict[x] for x in clust]
    # Getting the best rand score
    matrix=np.array(test_df)
    distance_thresholds=np.linspace(0,np.max(matrix),1000)
    best_rand = 0
    for d in distance_thresholds:
        clusters = get_clusters(matrix,threshold=d,method=method)
        rand=adjusted_rand_score(clust_as_float,clusters)
        if rand>best_rand:
            best_rand=rand
            best_mi=normalized_mutual_info_score(clust_as_float,clusters)
            best_threshold=d
    return best_rand, best_mi, best_threshold/mean_val/std_val

# Reading data with rand scores
rand_scores = pd.read_csv('./rand_score_errorbars_new.csv')

# Generate all the names for the matrixes we are about to extract
embeddings = ['AB2','ESM2','OHE','SONIA']
modifications = ['original','only_flanked','length','length_flanking',
                 'uniq_length','clonal_pat','clonal_all_df']
column_titles = ['original',
                 'flanking',
                 'length filtering',
                 'flanking+length filtering',
                 'unique sequences',
                 'clonal filtering within a donor',
                 'single linkage clustering across all donors']
plot_dict = {}
for i,j in zip(modifications,column_titles):
  plot_dict[i]=j
variants = list(itertools.product(embeddings,modifications))
variants.extend([('Jaccard','original'),
                 ('Jaccard','only_flanked'),
                 ('Jaccard','length'),
                 ('Jaccard','length_flanking')])
heatmaps = ['_'.join(x) for x in variants]

# Get information about all matrices that we need
linkages, clusts, palettes,aris,thresholds = [], [], [],[],[]
for i,heatmap in tqdm(enumerate(variants)):
        embed,modification = heatmap[0],heatmap[1]
        matrix,clust,palette= load_matrix(embed,modification)
        seriated_matrix,order,res_linkage= compute_serial_matrix(matrix,method='ward')
        rand_score, best_threshold = get_rand_score(embed,modification)[0],get_rand_score(embed,modification)[2]
        linkages.append(res_linkage)
        clusts.append(clust)
        palettes.append(palette)
        aris.append(rand_score)
        thresholds.append(best_threshold)

# Constructing color palettes for leaves in dendrograms
palettes_real = []
for i in range(len(linkages)):
    res_linkage = linkages[i]
    Z = dendrogram(res_linkage,
                  color_threshold=thresholds[i],
                   no_plot=True
                  )
    palette = Z['leaves_color_list']
    palettes_real.append(palette)


# Final plot construction
final_embeddings = ['AB2','ESM2','OHE','LEFTRIGHT','JACCARD']
plt.figure(figsize=(42,20),dpi=600)
aris = rand_scores['median'].tolist()
for i in range(len(linkages)):
    res_linkage = linkages[i]
    clust = clusts[i]
    rand_score = aris[i]
    patients_dict = {'316188':0, '326650':1, '326651':2,'326713':3, '326737':4,
                     '326780':5,'326797':6, '326907':7,'327059':8, 'D103':9}
    patients = set(clust)
    colors_for_w2 = sns.color_palette()[0:10]
    color_dict = dict(zip(range(0,10),colors_for_w2))

    ax=plt.subplot(len(embeddings)+1,len(modifications),i+1)

    if i%len(modifications)==0:
        plt.ylabel(final_embeddings[i//len(modifications)],fontsize=35)
    if i < len(modifications):
        plt.title(f'{plot_dict[modifications[i]]} \n\n Adjusted Rand Index = {round(rand_score,3)}',fontsize=20)
    else:
        plt.title(f'Adjusted Rand Index = {round(rand_score,3)}',fontsize=20)
    Z = dendrogram(res_linkage,
                   link_color_func=lambda k: 'black'
                   )
    plt.yscale('symlog')
    max_value = plt.ylim()[-1]
    a,b=plt.xticks()
    for j,k in enumerate(a):
        plt.plot([k,k],[0,-max_value/50],color=palettes_real[i][j],linewidth=2,alpha=0.5)
    plt.ylim([-max_value/50,max_value])
    plt.xticks([],[])
    plt.yticks([],[])
    ax = plt.gca()  # Get current axes
    for spine in ax.spines.values():
        spine.set_visible(False)


plt.subplots_adjust(wspace=0.1, hspace=0.5)
plt.tight_layout()
plt.savefig('Fig_S5_new.png',dpi=600)

32it [01:38,  3.07s/it]


32it [00:00, 68.47it/s]
